<span style="font-size: 14pt">MIPT, Advanced ML, Autumn 2017</span>

<span style="font-size: 16pt"> HW #9: Recommendation System

<span style="color:blue; font-size: 12pt">Andrey Saitgalin </span>
<span style="color:blue; font-size: 12pt; font-family: 'Verdana'">andrey.saitgalin@gmail.com</span>, 

<span style="color:blue; font-size: 12pt">Alexey Dral </span>,
<span style="color:blue; font-size: 12pt; font-family: 'Verdana'">aadral@gmail.com</span>

<h1 align="center">Organization Info</h1> 

**Дополнительный материал для выполнения дз**:
<a href= "https://github.com/ml-mipt/ml-mipt-part2/tree/master/2017/lectures">Лекции по курсу</a>

**Оформление дз**: 
- Присылайте выполненное задание на почту ``ml.course.mipt@gmail.com``
- Укажите тему письма в следующем формате ``ML2017_Aut_fall <номер_группы> <фамилия>``, к примеру -- ``ML2017_Aut_fall 401 ivanov``
- Выполненное дз сохраните в файл ``<фамилия>_<группа>_task<номер>.ipnb``, к примеру -- ``ivanov_491_task9.ipnb``

**Вопросы**:
- Присылайте вопросы на почту ``ml.course.mipt@gmail.com``
- Укажите тему письма в следующем формате ``ML2017_Aut_fall Question <Содержание вопроса>``

** Дедлайн**:
<span style="color:red; font-size: 12pt">16.12.2017 23:59 </span>

--------
- **PS1**: Мы используем автоматические фильтры, и просто не найдем ваше дз, если вы не аккуратно его подпишите.
- **PS2**: Напоминаем, что дедлайны жесткие, письма пришедшие после автоматически удаляются =( чтобы соблазна не было.

<h1 align="center">Check Questions (0%)</h1> 
Вопросы отсутствуют

## loading data

In [1]:
import pandas as pd
import numpy as np
import random

In [2]:
n = 20000263
s = 50000

skip = sorted(random.sample(range(1,n), n-s))

In [3]:
#tags = pd.read_csv('ml-20m/tags.csv')
movies = pd.read_csv('ml-20m/movies.csv', skiprows=skip)
ratings = pd.read_csv('ml-20m/ratings.csv',skiprows=skip)
#genome_scores = pd.read_csv('ml-20m/genome-scores.csv')
#genome_tags = pd.read_csv('ml-20m/genome-tags.csv')
links = pd.read_csv('ml-20m/links.csv', skiprows=skip)

In [21]:
links.head()

movieId  imdbId   tmdbId
0        1  114709    862.0
1        2  113497   8844.0
2        3  113228  15602.0
3        4  114885  31357.0
4        5  113041  11862.0

In [17]:
ratings.head()

userId  movieId  rating   timestamp
0       1        2     3.5  1112486027
1       1       29     3.5  1112484676
2       1       32     3.5  1112484819
3       1       47     3.5  1112484727
4       1       50     3.5  1112484580

In [20]:
movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

<h1 align="center"> Practical tasks (100%)</h1>


# Построение content-based рекомендательной системы
## Part 1
Для каждого фильма получите описание в текстовом виде с IMDB или (и) The movie database (у них есть открытое API). https://www.themoviedb.org/?language=ru. Вывести описание фильма под id 778. Также можно использовать рецензии.

In [1]:
f_id = 778

In [10]:
import requests

In [24]:
desc_cache = {}

In [30]:

def fetch_desc_by(f_id):
    if f_id in desc_cache:
        return desc_cache[f_id]
    else:
        json = requests.get('https://api.themoviedb.org/3/movie/'+f_id+'?api_key=b0da6cc7b6f4069733a9a354e88a0c15&language=en-US').json()
        print(json)
        if 'overview' in json:
            return json['overview']
        else:
            return ''

In [4]:
desc= fetch_desc_by(str(778))

{'adult': False, 'backdrop_path': '/zF95knRgouUrBNbUh5oqRI5NIcE.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}], 'homepage': '', 'id': 778, 'imdb_id': 'tt0046487', 'original_language': 'fr', 'original_title': 'Les vacances de Monsieur Hulot', 'overview': 'Monsieur Hulot, Jacques Tati’s endearing clown, takes a holiday at a seaside resort, where his presence provokes one catastrophe after another. Tati’s masterpiece of gentle slapstick is a series of effortlessly well-choreographed sight gags involving dogs, boats, and firecrackers; it was the first entry in the Hulot series and the film that launched its maker to international stardom.', 'popularity': 4.765439, 'poster_path': '/r4F4tsU0Ajeh9ZYUkWOJSYmioj7.jpg', 'production_companies': [{'name': 'Cady', 'id': 478}, {'name': 'Discina', 'id': 479}], 'production_countries': [{'iso_3166_1': 'FR', 'name': 'France'}], 'release_date': '1953-02-26', 'revenue': 0, 'runti

## Part 2 
Извлеките текстовые признаки у фильмов: tf idf, биграммы (может какие-то еще). Биграммы - статистика по биграммам, сколько какая биграмма встречается. Формулы для TF-IDF смотреть тут: https://en.wikipedia.org/wiki/Tf%E2%80%93idf 
    1. Используйте TF с double 0.5 normalization
    2. Используйте стандартный IDF: 
$$idf(t, D) = \frac{log N}{(1 + |d in D : t in d|)}$$

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer

In [8]:
tf = TfidfVectorizer(ngram_range=(1,2), min_df=0.5)

In [7]:
tf.fit_transform([desc]).todense()

matrix([[ 0.08873565,  0.08873565,  0.1774713 ,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.1774713 ,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.08873565,
          0.08873565,  0.08873565,  0.08873565,  0.08873565,  0.1774713 ,
          0.08873565,  0.08873565,  0.

## Part 3 
Выведите подсчитанные признаки из пункта 2 для фильма с id 99114.

In [11]:
desc = fetch_desc_by(str(99114))

{'status_code': 34, 'status_message': 'The resource you requested could not be found.'}


KeyError: 'overview'

## fetching movies desc from tmbd

In [12]:
mids = movies['movieId'].unique()

In [13]:
def get_tmdbid(mid):
    return links[links['movieId'] == mid].iloc[0,2]

In [27]:
mlen = len(mids)
tmdbids = np.zeros(mlen)

descs = []

for i in range(mlen):
    tmdbids[i] = get_tmdbid(mids[i])
    descs.append(fetch_desc_by(str(tmdbids[i])))

{'adult': False, 'backdrop_path': '/9Jos0a1BIZMoaBbgObnHHugFGdF.jpg', 'belongs_to_collection': None, 'budget': 10000000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}], 'homepage': '', 'id': 11861, 'imdb_id': 'tt0113347', 'original_language': 'en', 'original_title': 'How To Make An American Quilt', 'overview': 'Soon-to-be-wed graduate student Finn Dodd develops cold feet when she suspects her fiancé is cheating on her. In order to clear her head, Finn visits her grandmother, Hy, and great aunt, Glady Joe Cleary, in Grasse, Calif. There, Finn learns that Hy and Glady Joe are members of a group of passionate quilters, and over the course of her visit she is regaled with tales of love and life by women who have collected rich experiences and much wisdom.', 'popularity': 3.738467, 'poster_path': '/wnWAZHbjX5Wj6hyb0gGmFdMADZk.jpg', 'production_companies': [{'name': 'Universal Pictures', 'id': 33}, {'name': 'Amblin Entertainment', 'id': 56}], 'production_countries'

{'adult': False, 'backdrop_path': '/6HoX25QQpauFGFjZ8rr250cHy0L.jpg', 'belongs_to_collection': None, 'budget': 12000000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 28, 'name': 'Action'}, {'id': 53, 'name': 'Thriller'}, {'id': 80, 'name': 'Crime'}], 'homepage': '', 'id': 12628, 'imdb_id': 'tt0119906', 'original_language': 'en', 'original_title': 'Playing God', 'overview': 'Stripped of his medical license after performing an operation while high on amphetamines, famed LA surgeon Dr Eugene Sands abandons his former life only to find himself crossing paths with Raymond Blossom, an infamous counterfeiter. Employed as a "gun-shot doctor" when Raymond\'s associates cannot risk visiting a hospital, Eugene is lured deep into the criminal world and becomes entangled with his boss\'s girlfriend.', 'popularity': 2.148353, 'poster_path': '/udip0tPcopdx8AF77StrXJRkLb5.jpg', 'production_companies': [{'name': 'Touchstone Pictures', 'id': 9195}], 'production_countries': [{'iso_3166_1': 'US', 'name'

{'adult': False, 'backdrop_path': '/xpHIp4ZQjmfLslA2O4yfOG8O700.jpg', 'belongs_to_collection': None, 'budget': 4000000, 'genres': [{'id': 28, 'name': 'Action'}, {'id': 12, 'name': 'Adventure'}, {'id': 18, 'name': 'Drama'}], 'homepage': '', 'id': 9764, 'imdb_id': 'tt0071411', 'original_language': 'ru', 'original_title': 'Дерсу Узала', 'overview': 'A military explorer meets and befriends a Goldi man in Russia’s unmapped forests. A deep and abiding bond evolves between the two men, one civilized in the usual sense, the other at home in the glacial Siberian woods.', 'popularity': 5.348921, 'poster_path': '/i9FpzTXUi2XYVPLEa6Nf65I4WgE.jpg', 'production_companies': [{'name': 'Daiei Studios', 'id': 881}, {'name': 'Mosfilm', 'id': 5120}, {'name': 'Atelier 41', 'id': 6091}], 'production_countries': [{'iso_3166_1': 'RU', 'name': 'Russia'}, {'iso_3166_1': 'JP', 'name': 'Japan'}], 'release_date': '1975-08-02', 'revenue': 0, 'runtime': 144, 'spoken_languages': [{'iso_639_1': 'ru', 'name': 'Pусский'

{'adult': False, 'backdrop_path': '/ybLhbC1mrgle04OUTQ8WZ50H7NM.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}], 'homepage': '', 'id': 42035, 'imdb_id': 'tt0089343', 'original_language': 'en', 'original_title': 'Insignificance', 'overview': "Four 1950s cultural icons (Albert Einstein, Marilyn Monroe, Joe DiMaggio, and Senator Joseph MacCarthy) who conceivably could have met but probably didn't, fictionally do so in this modern fable of post-WWII America. Visually intriguing, the film has a fluid progression of flash-backs and flash-forwards centering on the fictional Einstein's current observations, childhood memories, and apprehensions for the future.", 'popularity': 1.753429, 'poster_path': '/ygTlITtPOLMcObTjf5o1DrmquXm.jpg', 'production_companies': [{'name': 'Zenith Entertainment', 'id': 3644}, {'name': 'Recorded Picture Company (RPC)', 'id': 11561}], 'production_countries': [{'iso_3166_1': 'GB', 'name': 'United

{'adult': False, 'backdrop_path': '/mncWOGmjvtH8PFtePIZ3VfNmgGA.jpg', 'belongs_to_collection': None, 'budget': 750000, 'genres': [{'id': 80, 'name': 'Crime'}, {'id': 18, 'name': 'Drama'}], 'homepage': '', 'id': 14135, 'imdb_id': 'tt0106341', 'original_language': 'en', 'original_title': 'Bad Boy Bubby', 'overview': 'Bad Boy Bubby is just that: a bad boy. So bad, in fact, that his mother has kept him locked in their house for his entire thirty years, convincing him that the air outside is poisonous. After a visit from his estranged father, circumstances force Bubby into the waiting world, a place which is just as unusual to him as he is to the world.', 'popularity': 3.211236, 'poster_path': '/tvipR7aVSsAbdfMlR4sbEqD1Pgd.jpg', 'production_companies': [{'name': 'Australian Film Finance Corporation', 'id': 1380}, {'name': 'Fandango', 'id': 2441}, {'name': 'South Australian Film Corporation', 'id': 2806}, {'name': 'Bubby Productions', 'id': 11263}], 'production_countries': [{'iso_3166_1': 'A

{'adult': False, 'backdrop_path': '/eivm9fvenuTJZxdiQzyLKRUqeLz.jpg', 'belongs_to_collection': {'id': 102008, 'name': 'Another Gay Movie Collection', 'poster_path': '/wpiTGGOmrAUWvxfIYStNfy32U62.jpg', 'backdrop_path': '/jhQG23R7yBtrWU9CV6konHkRkjd.jpg'}, 'budget': 500000, 'genres': [{'id': 35, 'name': 'Comedy'}, {'id': 10749, 'name': 'Romance'}], 'homepage': 'http://www.profun.de/anothergaymovie/', 'id': 12795, 'imdb_id': 'tt0443431', 'original_language': 'en', 'original_title': 'Another Gay Movie', 'overview': 'In the dirtiest, funniest, most scandalous gay-teen-sex-comedy-parody ever, four young gay friends make a pact to lose their virginity by the end of the summer. The boys soon face giant sex toys, naked celebrities, masochistic teachers and an uncontrollable romance with a quiche.', 'popularity': 4.160748, 'poster_path': '/x2YpUSvTXBMfUeA4IlvvtlfCjjy.jpg', 'production_companies': [{'name': 'TLA Releasing', 'id': 328}, {'name': 'Luna Filmproduktion', 'id': 402}], 'production_coun

{'adult': False, 'backdrop_path': '/7p7FIvssqsYUAdmhbgHSExzNk9D.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 80, 'name': 'Crime'}], 'homepage': 'http://www.mymovies.it/gomorra/', 'id': 8882, 'imdb_id': 'tt0929425', 'original_language': 'it', 'original_title': 'Gomorra', 'overview': 'An inside look at Italy\'s modern-day crime families, the Camorra in Naples and Caserta. Based on a book by Roberto Saviano. Power, money and blood: these are the "values" that the residents of the Province of Naples and Caserta have to face every day. They hardly ever have a choice and are forced to obey the rules of the Camorra. Only a lucky few can even think of leading a normal life.', 'popularity': 8.611214, 'poster_path': '/6aVJi30jxywKXbrpcBD11AuVoKv.jpg', 'production_companies': [{'name': 'Fandango', 'id': 2441}, {'name': 'Rai Cinema', 'id': 2683}, {'name': 'The Criterion Collection', 'id': 10932}], 'production_countries': [{'iso_3166_1': 'IT', 'na

{'adult': False, 'backdrop_path': '/d4yGhn8oHoTZM1TUVph1K1lDAIy.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 99, 'name': 'Documentary'}], 'homepage': '', 'id': 17602, 'imdb_id': 'tt1379667', 'original_language': 'en', 'original_title': 'Macheads', 'overview': 'A exploration of the fanaticism that surrounds the Apple brand, featuring interviews with Mac evangelists and members of the Mac community.', 'popularity': 0.286857, 'poster_path': '/pyvcFdMtmeRTiR29Hy2KQPEoLTS.jpg', 'production_companies': [], 'production_countries': [], 'release_date': '2009-01-01', 'revenue': 0, 'runtime': 54, 'spoken_languages': [], 'status': 'Released', 'tagline': '', 'title': 'Macheads', 'video': False, 'vote_average': 5.5, 'vote_count': 4}
{'adult': False, 'backdrop_path': '/qUYYlypyaaXGIZC3KCOAeO4pEZp.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 80, 'name': 'Crime'}, {'id': 18, 'name': 'Drama'}, {'id': 27, 'name': 'Horror'}], 'homepage': '', 'id': 42530, 'imdb

{'adult': False, 'backdrop_path': None, 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 28, 'name': 'Action'}, {'id': 27, 'name': 'Horror'}, {'id': 878, 'name': 'Science Fiction'}], 'homepage': '', 'id': 48038, 'imdb_id': 'tt0112993', 'original_language': 'en', 'original_title': 'Evolver', 'overview': "Meet Evolver, the ultimate toy for the Cyberpunk generation, a virtual-reality game brought to fierce, three-dimensional life. With each battle, Evolver lives up to his name. He becomes faster, smarter and deadlier. Meet Kyle Baxter (Ethan Randall) the teenage video game whiz who wins the first ever Evolver robot. Suddenly, some fatal accidents begin to happen. With help from Jamie Saunders (Cassidy Rae), a beautiful rival game player, Kyle digs up a terrifying missing link: Evo was created from a scrapped U.S. Defense Robotics Department. Designed to infiltrate enemy encampments, he has the capacity to adapt to any situation, and he's programmed to leave no survivors. By t

KeyError: 'overview'

In [36]:
links.head()

movieId  imdbId  tmdbId
0       31  112792    9909
1     1458  120357   61563
2     6820  210070    9871
3    27604  312843   12720
4    42728  375154    9044

In [15]:
tf.fit(descs)

TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=0.5,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=None, strip_accents=None, sublinear_tf=False,
        token_pattern='(?u)\\b\\w\\w+\\b', tokenizer=None, use_idf=True,
        vocabulary=None)

## Part 4
Для каждого пользователя найдите топ жанров, которые нравятся пользователю (можно делать как на семинаре top 5, top 3 и top 2) и порекомендуйте таким пользователя фильмы близкие по текстовому описанию (см. пункт 2). Для оценки результатов пункта 3 используйте метрику HitRate и метрики ранжирования (N)DCG. Формулу для подсчета HitRate можно взять на семинаре,  (N)DCG: https://en.wikipedia.org/wiki/Discounted_cumulative_gain



In [10]:
movies.head()

3008                          Last Night (1998)  \
0   3693                  Toxic Avenger, The (1985)   
1   8619                    Sister My Sister (1994)   
2  48879                        Catch a Fire (2006)   
3  58293                           10,000 BC (2008)   
4  84475  Rise and Fall of Legs Diamond, The (1960)   

                 Drama|Sci-Fi  
0               Comedy|Horror  
1                       Drama  
2              Drama|Thriller  
3  Adventure|Romance|Thriller  
4                       Crime

In [22]:
users = []
descs = []

In [16]:
from collections import Counter

genres = []

for row in movies.itertuples():
    genre_list = row.genres.split("|")
    genres.extend(genre_list)

cntr = Counter(genres)

In [17]:
df_joined = pd.merge(ratings, movies[["movieId", "genres"]], on="movieId", how="inner")

In [18]:
def genre_list(x):
    return list(set("|".join(x.tolist()).split("|")))

def genre_list_len(x):
    return len(genre_list(x))

def popular_genres(x):
    return Counter("|".join(x.tolist()).split("|")).most_common(3)

df_users = df_joined.groupby('userId').agg({'genres': [genre_list, genre_list_len, popular_genres]})

In [16]:
df_users.head()

genres                              
       genre_list genre_list_len popular_genres
userId                                         
47901     [Drama]              1   [(Drama, 1)]
52609     [Drama]              1   [(Drama, 1)]
86496     [Drama]              1   [(Drama, 1)]

In [19]:
def run_cv(predictor_class, fold_count=5, top_size=10):
    users = list(range(len(ratings["userId"].unique())))
    fold_size = len(users) // fold_count

    results = []

    for fold_start in range(fold_count):
        fold = users[fold_start:fold_start+fold_size]

        ratings["random"] = np.random.random(size=(ratings.shape[0], 1))
        idx = ratings.sort_values(by="random") \
            .reset_index() \
            .groupby("userId") \
            .last()["index"]

        mask = ratings.index.isin(idx) & ratings["userId"].isin(fold)
        train_df = ratings[~mask]
        test_df = ratings[mask]

        predictor = predictor_class(train_df, test_df)
        
        sum_ = 0.0
        for row in ratings.itertuples():
            prediction = predictor.predict(row)
            if prediction is None:
                continue
                
            sum_ += float(row.movieId in prediction)

        results.append(sum_ / test_df.shape[0])
    
    return np.mean(results)

In [20]:
top_size = 10

In [21]:
class PopularityPredictor(object):
    def __init__(self, train_df, test_df):
        self.top = list(train_df
            .groupby("movieId")
            .size()
            .reset_index()
            .sort_values(by=0, ascending=False)
            .iloc[:top_size]["movieId"]
            .values)

    def predict(self, row):
        return self.top

run_cv(PopularityPredictor)

0.91502727849287635

In [41]:
ratings.head()

userId  movieId  rating   timestamp    random
0       1     1259     4.0  1112485440  0.544015
1       1     2138     4.0  1112485789  0.381687
2       1     5026     4.0  1112485858  0.818017
3       2     3928     5.0   974820776  0.869578
4       7     3448     4.0  1011206092  0.926922

In [42]:
links.head()

movieId  imdbId  tmdbId
0       46  113347   11861
1       72  113537   28387
2      134  114500  124636
3      235  109707     522
4      757  109688   40751

In [53]:
class MyTestPredictor(object):
    def __init__(self, train_df, test_df):
        mids = train_df['movieId']
        #print(mid)
        for mid in mids:
            desc = fetch_desc_by(str(mid))
            
        print(desc)
    
    def predict(self, row):
        pass

In [ ]:
run_cv(MyTestPredictor)

{'adult': False, 'backdrop_path': '/npmNXZNo3uQvJghUfzXWUEm3J3J.jpg', 'belongs_to_collection': None, 'budget': 15000000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}], 'homepage': 'http://www.foxsearchlight.com/NOAS/', 'id': 1259, 'imdb_id': 'tt0465551', 'original_language': 'en', 'original_title': 'Notes on a Scandal', 'overview': 'A veteran high school teacher befriends a younger art teacher, who is having an affair with one of her 15-year-old students. However, her intentions with this new "friend" also go well beyond platonic friendship.', 'popularity': 8.640604, 'poster_path': '/lXZa1mHZ8eD0VOpNaLfvM9tSpAj.jpg', 'production_companies': [{'name': 'Fox Searchlight Pictures', 'id': 43}, {'name': 'Scott Rudin Productions', 'id': 258}, {'name': 'DNA Films', 'id': 284}, {'name': 'BBC Films', 'id': 288}, {'name': 'Ingenious Film Partners', 'id': 289}, {'name': 'UK Film Council', 'id': 2452}], 'production_countries': [{'iso_3166_1': 'GB', 'name': 'United Kingdo

{'adult': False, 'backdrop_path': '/unmI2cUB0RvlpXj7AfSgphzDsUt.jpg', 'belongs_to_collection': {'id': 31562, 'name': 'The Bourne Collection', 'poster_path': '/lTfOZ25PhQkmGb5NHmaFnwB7b13.jpg', 'backdrop_path': '/vA5xMglyZv7yzDTj1qUTU4OvelV.jpg'}, 'budget': 75000000, 'genres': [{'id': 28, 'name': 'Action'}, {'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}], 'homepage': 'https://www.uphe.com/movies/the-bourne-supremacy', 'id': 2502, 'imdb_id': 'tt0372183', 'original_language': 'en', 'original_title': 'The Bourne Supremacy', 'overview': 'When a CIA operation to purchase classified Russian documents is blown by a rival agent, who then shows up in the sleepy seaside village where Bourne and Marie have been living. The pair run for their lives and Bourne, who promised retaliation should anyone from his former life attempt contact, is forced to once again take up his life as a trained assassin to survive.', 'popularity': 14.670109, 'poster_path': '/jXwZgmqOtsqsXuB9oGhocOAegCM.jpg',

{'adult': False, 'backdrop_path': '/eSZUjmpNSnQZ2Wp1IRdlbUpSAuz.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 12, 'name': 'Adventure'}, {'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}], 'homepage': '', 'id': 175, 'imdb_id': 'tt0095250', 'original_language': 'fr', 'original_title': 'Le Grand Bleu', 'overview': 'Two men answer the call of the ocean in this romantic fantasy-adventure.  Jacques (Jean-Marc Barr) and Enzo (Jean Reno) are a pair of friends who have been close since childhood, and who share a passion for the dangerous sport of free diving. Professional diver Jacques opted to follow in the footsteps of his father, who died at sea when Jacques was a boy; to the bewilderment of scientists, Jacques harbors a remarkable ability to adjust his heart rate and breathing pattern in the water, so that his vital signs more closely resemble that of dolphins than men (he even considers a school of dolphins as his extended family).  As Enzo persuades a rel

{'adult': False, 'backdrop_path': '/8AFuElrPnUaasD9Vl3usyUbUUqa.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 28, 'name': 'Action'}, {'id': 27, 'name': 'Horror'}, {'id': 878, 'name': 'Science Fiction'}, {'id': 53, 'name': 'Thriller'}], 'homepage': '', 'id': 1702, 'imdb_id': 'tt0109575', 'original_language': 'en', 'original_title': 'Death Machine', 'overview': "Chaank Armaments is experimenting with the ultimate fighting machine which is part human - part machine. So far, the Hardman project has been unreliable and has killed a number of innocent people. The genius behind this project is Jack who lives in a world of models, toys and magazines. When he is fired by Cale for killing a few corporate officers, he unleashes the ultimate killing machine called the 'Warbeast' against Cale and those who would help her.", 'popularity': 4.856678, 'poster_path': '/yg9zyB7CgbfUTXY0FQb2rUB0HYa.jpg', 'production_companies': [{'name': 'Fugitive Features', 'id': 1625}], 'production

{'adult': False, 'backdrop_path': None, 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 80, 'name': 'Crime'}], 'homepage': '', 'id': 6149, 'imdb_id': 'tt0179827', 'original_language': 'en', 'original_title': 'Glatteis', 'overview': 'No overview found.', 'popularity': 0.012554, 'poster_path': '/mp82tda1YiVHE4hni9kZMuzqTMG.jpg', 'production_companies': [], 'production_countries': [{'iso_3166_1': 'DE', 'name': 'Germany'}], 'release_date': '1998-01-01', 'revenue': 0, 'runtime': 90, 'spoken_languages': [{'iso_639_1': 'de', 'name': 'Deutsch'}], 'status': 'Released', 'tagline': '', 'title': 'Glatteis', 'video': False, 'vote_average': 0.0, 'vote_count': 0}
{'adult': False, 'backdrop_path': '/548GYgrjMIhjGXutwTALVxg9xqI.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}, {'id': 878, 'name': 'Science Fiction'}], 'homepage': '', 'id': 27834, 'imdb_id': 'tt0254199', 'original_language': 'en', 'original_title': 'CQ', 

...

{'adult': False, 'backdrop_path': '/mcFPTYm90593alFemhEMZIaiMa6.jpg', 'belongs_to_collection': {'id': 133830, 'name': 'Star Wars: The Ewok Adventures Collection', 'poster_path': '/iY9Smj4RQB1ey8QB0JcMtV35uc1.jpg', 'backdrop_path': '/9IwrTRYGaxrlbRjCs7UBRzU0skS.jpg'}, 'budget': 3000000, 'genres': [{'id': 12, 'name': 'Adventure'}, {'id': 10751, 'name': 'Family'}, {'id': 14, 'name': 'Fantasy'}, {'id': 878, 'name': 'Science Fiction'}, {'id': 10770, 'name': 'TV Movie'}], 'homepage': '', 'id': 1884, 'imdb_id': 'tt0087225', 'original_language': 'en', 'original_title': 'The Ewok Adventure', 'overview': "The Towani family civilian shuttlecraft crashes on the forest moon of Endor. The four Towani's are separated. Jermitt and Catarine, the mother and father are captured by the giant Gorax, and Mace and Cindel, the son and daughter, are missing when they are captured. The next day, the Ewok Deej is looking for his two sons when they find Cindel all alone in the shuttle (Mace and Cindel were lookin

{'adult': False, 'backdrop_path': '/7gTlxte4Oyp1TjWZieThQPmmraz.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 878, 'name': 'Science Fiction'}], 'homepage': '', 'id': 3418, 'imdb_id': 'tt0081182', 'original_language': 'fr', 'original_title': 'La Mort en direct', 'overview': 'Roddy has a camera implanted in his brain. He is then hired by a television producer to film a documentary of terminally ill Katherine, without her knowledge. His footage will then be run on the popular TV series, "Death Watch".', 'popularity': 1.273603, 'poster_path': '/lrsi268dfiQJGvd0eLtQTMwj33d.jpg', 'production_companies': [{'name': 'Films A2', 'id': 875}, {'name': 'Sara Films', 'id': 876}, {'name': 'Société Française de Production (SFP)', 'id': 6849}, {'name': 'Gaumont International', 'id': 7961}, {'name': 'TV13 Filmproduktion', 'id': 9246}, {'name': 'Little Bear', 'id': 16772}], 'production_countries': [{'iso_3166_1': 'DE', 'name': 'Germany'}, {'iso_3166_1': 

{'adult': False, 'backdrop_path': '/cYd3PL27r0KJa9Pa4A5lfUr58Yg.jpg', 'belongs_to_collection': None, 'budget': 28000000, 'genres': [{'id': 14, 'name': 'Fantasy'}, {'id': 27, 'name': 'Horror'}, {'id': 28, 'name': 'Action'}], 'homepage': 'http://www.dawnofthedeadmovie.net/', 'id': 924, 'imdb_id': 'tt0363547', 'original_language': 'en', 'original_title': 'Dawn of the Dead', 'overview': 'A group of surviving people take refuge in a shopping center after the world has been over taken over by aggressive, flesh-eating zombies. A remake of the 1978 zombie film of the same name.', 'popularity': 24.780758, 'poster_path': '/yfqsgzW6AQYmBjIEIq0y9EB1Rgl.jpg', 'production_companies': [{'name': 'New Amsterdam Entertainment', 'id': 572}, {'name': 'Strike Entertainment', 'id': 655}, {'name': 'Metropolitan Filmexport', 'id': 656}, {'name': 'Toho-Towa', 'id': 657}, {'name': 'Cruel and Unusual Films', 'id': 78685}], 'production_countries': [{'iso_3166_1': 'US', 'name': 'United States of America'}], 'relea

{'adult': False, 'backdrop_path': '/sFpGI08aeHIRKlLi9SxLyYrRyZ8.jpg', 'belongs_to_collection': None, 'budget': 150000000, 'genres': [{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}, {'id': 14, 'name': 'Fantasy'}], 'homepage': 'http://disney.go.com/disneypictures/ratatouille/', 'id': 2062, 'imdb_id': 'tt0382932', 'original_language': 'en', 'original_title': 'Ratatouille', 'overview': "A rat named Remy dreams of becoming a great French chef despite his family's wishes and the obvious problem of being a rat in a decidedly rodent-phobic profession. When fate places Remy in the sewers of Paris, he finds himself ideally situated beneath a restaurant made famous by his culinary hero, Auguste Gusteau. Despite the apparent dangers of being an unlikely - and certainly unwanted - visitor in the kitchen of a fine French restaurant, Remy's passion for cooking soon sets into motion a hilarious and exciting rat race that turns the culinary world of Paris

{'adult': False, 'backdrop_path': '/mrB9FWjNgIm21zXckWleZxG7fys.jpg', 'belongs_to_collection': {'id': 498, 'name': 'Heart of Gold Collection', 'poster_path': '/cwrmUIVzOuR9FdqKBfERkMHdde0.jpg', 'backdrop_path': '/293UTX2btTkblOL7WZF1Q7veIJm.jpg'}, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}], 'homepage': '', 'id': 145, 'imdb_id': 'tt0115751', 'original_language': 'da', 'original_title': 'Breaking the Waves', 'overview': "In a small and conservative Scottish village, a woman's paralytic husband convinces her to have extramarital intercourse so she can tell him about it and give him a reason for living.", 'popularity': 6.681183, 'poster_path': '/ffEFzMQ9Ee0SkwmCQvwD6MAOfl5.jpg', 'production_companies': [{'name': 'Trust Film', 'id': 123}, {'name': 'Danish Film Institute', 'id': 125}], 'production_countries': [{'iso_3166_1': 'DK', 'name': 'Denmark'}, {'iso_3166_1': 'FR', 'name': 'France'}, {'iso_3166_1': 'IS', 'name': 'Iceland'}, {'iso_3166_1': 'NL